In [1]:
import logging
import argparse
import math
import os
import sys
from time import strftime, localtime
import random
import numpy

from pytorch_transformers import BertModel
from models.knowledge_bert import BertForTokenClassification

from sklearn import metrics
import torch
import torch.nn as nn
from torch.utils.data import DataLoader, random_split

from data_utils import build_tokenizer, build_embedding_matrix, Tokenizer4Bert, ABSADataset

from models import LSTM, IAN, MemNet, RAM, TD_LSTM, Cabasc, ATAE_LSTM, TNet_LF, AOA, MGAN, LCF_BERT
from models.aen import CrossEntropyLoss_LSR, AEN_BERT
from models.bert_spc import BERT_SPC
from models.bert_raw import BERT_RAW
from models.bert_label import BERT_LABEL
from models.bert_aspect import BERT_ASPECT
from models.bert_kg import BERT_KG
logger = logging.getLogger()
logger.setLevel(logging.INFO)
logger.addHandler(logging.StreamHandler(sys.stdout))

torch.cuda.set_device(5)
import numpy as np

Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex.


In [2]:
dataset_files = {
'twitter': {
    'train': './datasets/acl-14-short-data/train.raw',
    'test': './datasets/acl-14-short-data/test.raw'
},
'restaurant': {
    'train': './datasets/semeval14/Restaurants_Train.xml.seg',
    'test': './datasets/semeval14/Restaurants_Test_Gold.xml.seg'
},
'laptop': {
    'train': './datasets/semeval14/Laptops_Train.xml.seg',
    'test': './datasets/semeval14/Laptops_Test_Gold.xml.seg'
}
}

In [3]:
parser = argparse.ArgumentParser()
parser.add_argument('--model_name', default='bert_spc', type=str)
parser.add_argument('--dataset', default='laptop', type=str, help='twitter, restaurant, laptop')
parser.add_argument('--optimizer', default='adam', type=str)
parser.add_argument('--initializer', default='xavier_uniform_', type=str)
parser.add_argument('--learning_rate', default=2e-5, type=float, help='try 5e-5, 2e-5 for BERT, 1e-3 for others')
parser.add_argument('--dropout', default=0.1, type=float)
parser.add_argument('--l2reg', default=0.01, type=float)
parser.add_argument('--num_epoch', default=10, type=int, help='try larger number for non-BERT models')
parser.add_argument('--batch_size', default=16, type=int, help='try 16, 32, 64 for BERT models')
parser.add_argument('--log_step', default=5, type=int)
parser.add_argument('--embed_dim', default=300, type=int)
parser.add_argument('--hidden_dim', default=300, type=int)
parser.add_argument('--bert_dim', default=768, type=int)
parser.add_argument('--pretrained_bert_name', default='bert-base-uncased', type=str)
parser.add_argument('--max_seq_len', default=80, type=int)
parser.add_argument('--polarities_dim', default=3, type=int)
parser.add_argument('--hops', default=3, type=int)
parser.add_argument('--device', default=None, type=str, help='e.g. cuda:0')
parser.add_argument('--seed', default=None, type=int, help='set seed for reproducibility')
parser.add_argument('--valset_ratio', default=0, type=float, help='set ratio between 0 and 1 for validation support')
parser.add_argument('--load_mode', default=0, type=int, help='load existed model')

# The following parameters are only valid for the lcf-bert model
parser.add_argument('--local_context_focus', default='cdm', type=str, help='local context focus mode, cdw or cdm')
parser.add_argument('--SRD', default=3, type=int, help='semantic-relative-distance, see the paper of LCF-BERT model')
opt = parser.parse_args([])

In [4]:
model_classes = {
        'lstm': LSTM,
        'td_lstm': TD_LSTM,
        'atae_lstm': ATAE_LSTM,
        'ian': IAN,
        'memnet': MemNet,
        'ram': RAM,
        'cabasc': Cabasc,
        'tnet_lf': TNet_LF,
        'aoa': AOA,
        'mgan': MGAN,
        'bert_spc': BERT_SPC,
        'aen_bert': AEN_BERT,
        'lcf_bert': LCF_BERT,
        'bert_raw': BERT_RAW,
        'bert_label': BERT_LABEL,
        'bert_aspect': BERT_ASPECT,
        'bert_kg': BERT_KG,
        # default hyper-parameters for LCF-BERT model is as follws:
        # lr: 2e-5
        # l2: 1e-5
        # batch size: 16
        # num epochs: 5
    }

In [5]:
opt.model_class = model_classes[opt.model_name]
opt.dataset_file = dataset_files[opt.dataset]
# opt.inputs_cols = input_colses[opt.model_name]
# opt.initializer = initializers[opt.initializer]
# opt.optimizer = optimizers[opt.optimizer]
opt.device = torch.device('cuda' if torch.cuda.is_available() else 'cpu') \
    if opt.device is None else torch.device(opt.device)

In [6]:
tokenizer = Tokenizer4Bert(opt.max_seq_len, opt.pretrained_bert_name)

loading file https://s3.amazonaws.com/models.huggingface.co/bert/bert-base-uncased-vocab.txt from cache at /home/nus/.cache/torch/pytorch_transformers/26bc1ad6c0ac742e9b52263248f6d0f00068293b33709fae12320c0e35ccfbbb.542ce4285a40d23a559526243235df47c5f75c197f04f37d1a0c124c32c9a084


In [7]:
def pad_and_truncate(sequence, maxlen, dtype='int64', padding='post', truncating='post', value=0):
    x = (np.ones(maxlen) * value).astype(dtype)
    if truncating == 'pre':
        trunc = sequence[-maxlen:]
    else:
        trunc = sequence[:maxlen]
    trunc = np.asarray(trunc, dtype=dtype)
    if padding == 'post':
        x[:len(trunc)] = trunc
    else:
        x[-len(trunc):] = trunc
    return x

In [8]:
fin = open(opt.dataset_file['train'], 'r', encoding='utf-8', newline='\n', errors='ignore')
lines = fin.readlines()
fin.close()

all_data = []
for i in range(0, len(lines), 3):
    text_left, _, text_right = [s.lower().strip() for s in lines[i].partition("$T$")]
    aspect = lines[i + 1].lower().strip()
    polarity = lines[i + 2].strip()

    text_raw="[CLS] " + text_left + " " + aspect + " " + text_right + " [SEP]"
    text_spc='[CLS] ' + text_left + " " + aspect + " " + text_right + ' [SEP] ' + aspect + " [SEP]"


    text_raw_indices = tokenizer.text_to_sequence(text_left + " " + aspect + " " + text_right)
    text_raw_without_aspect_indices = tokenizer.text_to_sequence(text_left + " " + text_right)
    text_left_indices = tokenizer.text_to_sequence(text_left)
    text_left_with_aspect_indices = tokenizer.text_to_sequence(text_left + " " + aspect)
    text_right_indices = tokenizer.text_to_sequence(text_right, reverse=True)
    text_right_with_aspect_indices = tokenizer.text_to_sequence(" " + aspect + " " + text_right, reverse=True)
    aspect_indices = tokenizer.text_to_sequence(aspect)
    left_context_len = np.sum(text_left_indices != 0)
    aspect_len = np.sum(aspect_indices != 0)
    aspect_in_text = torch.tensor([left_context_len.item(), (left_context_len + aspect_len - 1).item()])
    polarity = int(polarity) + 1

    text_bert_indices = tokenizer.text_to_sequence('[CLS] ' + text_left + " " + aspect + " " + text_right + ' [SEP] ' + aspect + " [SEP]")
    bert_segments_ids = np.asarray([0] * (np.sum(text_raw_indices != 0) + 2) + [1] * (aspect_len + 1))
    bert_segments_ids = pad_and_truncate(bert_segments_ids, tokenizer.max_seq_len)

    text_raw_bert_indices = tokenizer.text_to_sequence("[CLS] " + text_left + " " + aspect + " " + text_right + " [SEP]")
    aspect_bert_indices = tokenizer.text_to_sequence("[CLS] " + aspect + " [SEP]")
    input_mask=torch.tensor([1]*len(text_bert_indices))

    data = {

                'text_raw': text_raw,
                'text_spc': text_spc,
                'text_aspect':aspect,
                'left_context_len': left_context_len,
                'text_bert_indices': text_bert_indices,
                'bert_segments_ids': bert_segments_ids,
                'text_raw_bert_indices': text_raw_bert_indices,
                'aspect_bert_indices': aspect_bert_indices,
                'text_raw_indices': text_raw_indices,
                'text_raw_without_aspect_indices': text_raw_without_aspect_indices,
                'text_left_indices': text_left_indices,
                'text_left_with_aspect_indices': text_left_with_aspect_indices,
                'text_right_indices': text_right_indices,
                'text_right_with_aspect_indices': text_right_with_aspect_indices,
                'aspect_indices': aspect_indices,
                'aspect_in_text': aspect_in_text,
                'polarity': polarity,
                'input_mask':input_mask,
            }

    all_data.append(data)

In [9]:
len(all_data)

2328

In [12]:
idx=0
while idx in range(len(all_data)):
    print(idx,'new')
    data=all_data[idx]
    text_raw=data['text_raw']
    flag = True
    count=0
    while flag:
#         idx=idx+1
        count=count+1
        if idx+count not in range(len(all_data)):
            break
        text_raw_next=all_data[idx+count]['text_raw']
        if (text_raw_next!=text_raw):
            flag=False
#     if count==1:
#         idx=idx+count
#         continue
    aspect_list=[]
    for i in range(0,count):
        aspect=all_data[idx+i]['text_aspect']
        aspect_list.append(aspect)
        all_data[idx+i]['text_multi']=aspect+all_data[idx+i]['text_raw']
#     print()
    for i in range(0,count):
#         print('i',i)
#         print('aspect_list',aspect_list)
#         print('aspect',aspect)
#         print('other_aspect',other_aspect)
        aspect=all_data[idx+i]['text_aspect']
        tt=aspect_list.copy()
        print(tt)
        tt.pop(i)
        other_aspect=tt
        print(other_aspect)
        if other_aspect is not None: 
            for other in other_aspect:
                print('other',other)
                all_data[idx+i]['text_multi']=all_data[idx+i]['text_multi']+other+' [SEP]'
    print(idx,count,len(aspect_list))
    idx=idx+count

0 new
['cord', 'battery life']
['battery life']
other battery life
['cord', 'battery life']
['cord']
other cord
0 2 2
2 new
['service center']
[]
2 1 1
3 new
['"sales" team']
[]
3 1 1
4 new
['tech guy']
[]
4 1 1
5 new
['quality', 'gui', 'applications', 'use']
['gui', 'applications', 'use']
other gui
other applications
other use
['quality', 'gui', 'applications', 'use']
['quality', 'applications', 'use']
other quality
other applications
other use
['quality', 'gui', 'applications', 'use']
['quality', 'gui', 'use']
other quality
other gui
other use
['quality', 'gui', 'applications', 'use']
['quality', 'gui', 'applications']
other quality
other gui
other applications
5 4 4
9 new
['start up']
[]
9 1 1
10 new
['features', 'ichat', 'photobooth', 'garage band']
['ichat', 'photobooth', 'garage band']
other ichat
other photobooth
other garage band
['features', 'ichat', 'photobooth', 'garage band']
['features', 'photobooth', 'garage band']
other features
other photobooth
other garage band
['featu

other programs
other photo booth
other iphoto
other imovie
other video-editing
other movie-making
other photo management
other music
other pages
other numbers
other keynote
other school or office use
['programs', 'garageband', 'photo booth', 'iphoto', 'imovie', 'video-editing', 'movie-making', 'photo management', 'music', 'pages', 'numbers', 'keynote', 'school or office use']
['programs', 'garageband', 'iphoto', 'imovie', 'video-editing', 'movie-making', 'photo management', 'music', 'pages', 'numbers', 'keynote', 'school or office use']
other programs
other garageband
other iphoto
other imovie
other video-editing
other movie-making
other photo management
other music
other pages
other numbers
other keynote
other school or office use
['programs', 'garageband', 'photo booth', 'iphoto', 'imovie', 'video-editing', 'movie-making', 'photo management', 'music', 'pages', 'numbers', 'keynote', 'school or office use']
['programs', 'garageband', 'photo booth', 'imovie', 'video-editing', 'movie-mak

['companies']
[]
975 1 1
976 new
['customer service']
[]
976 1 1
977 new
['plug']
[]
977 1 1
978 new
['hdd cover']
[]
978 1 1
979 new
['applications']
[]
979 1 1
980 new
['design']
[]
980 1 1
981 new
['keyboard']
[]
981 1 1
982 new
['iphoto', 'program']
['program']
other program
['iphoto', 'program']
['iphoto']
other iphoto
982 2 2
984 new
['spy ware', 'nortell']
['nortell']
other nortell
['spy ware', 'nortell']
['spy ware']
other spy ware
984 2 2
986 new
['videocard']
[]
986 1 1
987 new
['price']
[]
987 1 1
988 new
['drivers']
[]
988 1 1
989 new
['speakers', 'keyboard']
['keyboard']
other keyboard
['speakers', 'keyboard']
['speakers']
other speakers
989 2 2
991 new
['use']
[]
991 1 1
992 new
['setting']
[]
992 1 1
993 new
['screen size', 'pixel sizes']
['pixel sizes']
other pixel sizes
['screen size', 'pixel sizes']
['screen size']
other screen size
993 2 2
995 new
['pre installed software update']
[]
995 1 1
996 new
['customer services', 'toshiba customer services']
['toshiba custome

1570 new
['speakers']
[]
1570 1 1
1571 new
['battery']
[]
1571 1 1
1572 new
['surfing the web']
[]
1572 1 1
1573 new
['iphoto']
[]
1573 1 1
1574 new
['senior tech']
[]
1574 1 1
1575 new
['volume wheel', 'sound quality', 'features']
['sound quality', 'features']
other sound quality
other features
['volume wheel', 'sound quality', 'features']
['volume wheel', 'features']
other volume wheel
other features
['volume wheel', 'sound quality', 'features']
['volume wheel', 'sound quality']
other volume wheel
other sound quality
1575 3 3
1578 new
['price']
[]
1578 1 1
1579 new
['manual', 'hard drive']
['hard drive']
other hard drive
['manual', 'hard drive']
['manual']
other manual
1579 2 2
1581 new
['software']
[]
1581 1 1
1582 new
['sensitivity']
[]
1582 1 1
1583 new
['battery']
[]
1583 1 1
1584 new
['battery life', 'case', 'core applications', 'system']
['case', 'core applications', 'system']
other case
other core applications
other system
['battery life', 'case', 'core applications', 'system'

other speed
1860 3 3
1863 new
['power supply cord', 'applecare warranty plan']
['applecare warranty plan']
other applecare warranty plan
['power supply cord', 'applecare warranty plan']
['power supply cord']
other power supply cord
1863 2 2
1865 new
['13 inch']
[]
1865 1 1
1866 new
['power supply']
[]
1866 1 1
1867 new
['screen']
[]
1867 1 1
1868 new
['use']
[]
1868 1 1
1869 new
['right speaker']
[]
1869 1 1
1870 new
['support']
[]
1870 1 1
1871 new
['final cut pro']
[]
1871 1 1
1872 new
['runs']
[]
1872 1 1
1873 new
['mac snow leopard o/s', 'win xp', 'visa', 'win7', 'use']
['win xp', 'visa', 'win7', 'use']
other win xp
other visa
other win7
other use
['mac snow leopard o/s', 'win xp', 'visa', 'win7', 'use']
['mac snow leopard o/s', 'visa', 'win7', 'use']
other mac snow leopard o/s
other visa
other win7
other use
['mac snow leopard o/s', 'win xp', 'visa', 'win7', 'use']
['mac snow leopard o/s', 'win xp', 'win7', 'use']
other mac snow leopard o/s
other win xp
other win7
other use
['mac 

In [24]:
all_data[0]['text_raw']

'[CLS] i charge it at night and skip taking the cord with me because of the good battery life . [SEP]'

In [48]:
s=all_data[0]['text_raw']
idx=all_data[0]['text_raw'].find('cord')
idx

47

In [93]:
def insert(original, new, pos):
# '''Inserts new inside original at pos.'''
    return original[:pos] + new + original[pos:]

aspect_list=['cord','battery life']
s=all_data[0]['text_raw']
aspect_cls=all_data[0]['text_aspect']
# text_left, _, text_right = [s.lower().strip() for s in lines[i].partition("$T$")]
print(aspect_cls)
for aspect in aspect_list:
    
    idx=s.find(aspect)
    s=insert(s,'[aspect_b] ',idx)
    idx=s.find(aspect)
    s=insert(s,' [aspect_e]',idx+len(aspect))
aspect_cls_idx=s.find(aspect_cls)

left = s[:aspect_cls_idx-len('[aspect_b] ')]
s_left_=tokenizer.text_to_sequence(left)
# print(left)
cls_pos=np.sum(s_left_ != 0)
# print(s_left_[cls_pos])

cord
[CLS] i charge it at night and skip taking the 
0


In [94]:
all_data[i]['bert_compete_cls']=cls_pos
            all_data[i]['bert_compete_indices']=bert_compete_indices
            all_data[i]['bert_compete_segments_ids']=bert_compete_segments_ids

IndentationError: unexpected indent (<ipython-input-94-908ed7c82900>, line 2)

In [62]:
all_data[0]['bert_segments_ids']

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1,
       1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0])

In [201]:
for i in range(len(all_data)):
            text_multi = all_data[i]['text_multi']
            text_raw= all_data[i]['text_raw']
            aspect_indices=all_data[i]['aspect_indices']
            # text
            bert_aspect_indices = tokenizer.text_to_sequence(text_multi)
            aspect_len = np.sum(aspect_indices != 0)
            before=np.asarray(([1] * (aspect_len)))
            mid=np.asarray([0] * (np.sum(text_bert_indices != 0)))
            after= np.asarray([1] * (np.sum(bert_aspect_indices != 0)-np.sum(text_bert_indices != 0)-aspect_len))
#             print(before)
#             print(mid)
#             print(after)
#             print(before+mid+after)
            bert_aspect_segments_ids=np.asarray(([1] * (aspect_len))+[0] * (np.sum(text_bert_indices != 0))+[1] * (np.sum(bert_aspect_indices != 0)-np.sum(text_bert_indices != 0)-aspect_len))
            print(np.sum(text_bert_indices != 0))
            print(len(bert_aspect_segments_ids)) 
#             bert_aspect_segments_ids= before.append(mid).append(after)
            bert_aspect_segments_ids = pad_and_truncate(bert_aspect_segments_ids, tokenizer.max_seq_len)
            all_data[i]['bert_aspect_indices']=bert_aspect_indices
            all_data[i]['bert_aspect_segments_ids']=bert_aspect_segments_ids

SyntaxError: invalid syntax (<ipython-input-201-2c3fa1ab9d6a>, line 17)

In [181]:
print(a)
for i in range(len(all_data)):
    print(i)
    print(all_data[i]['text_multi'])


None
0
cord[CLS] i charge it at night and skip taking the cord with me because of the good battery life . [SEP]battery life [SEP]
1
battery life[CLS] i charge it at night and skip taking the cord with me because of the good battery life . [SEP]cord [SEP]
2
service center[CLS] the tech guy then said the service center does not do 1-to-1 exchange and i have to direct my concern to the `` sales '' team , which is the retail shop which i bought my netbook from . [SEP]
3
"sales" team[CLS] the tech guy then said the service center does not do 1-to-1 exchange and i have to direct my concern to the "sales" team , which is the retail shop which i bought my netbook from . [SEP]
4
tech guy[CLS] the tech guy then said the service center does not do 1-to-1 exchange and i have to direct my concern to the `` sales '' team , which is the retail shop which i bought my netbook from . [SEP]
5
quality[CLS] it is of high quality , has a killer gui , is extremely stable , is highly expandable , is bundled w

runs[CLS] the battery holds up well , it 's built very solidly , and runs fast . [SEP]battery [SEP]built [SEP]
1534
sound card[CLS]  sound card is limited though . [SEP]
1535
processing power[CLS] this is a nicely sized laptop with lots of processing power and long battery life . [SEP]battery life [SEP]sized [SEP]
1536
battery life[CLS] this is a nicely sized laptop with lots of processing power and long battery life . [SEP]processing power [SEP]sized [SEP]
1537
sized[CLS] this is a nicely sized laptop with lots of processing power and long battery life . [SEP]processing power [SEP]battery life [SEP]
1538
vista[CLS] the only thing i can imagine is that sony jumped on early specifications for vista requirements from microsoft and designed it to those inadequate requirements . [SEP]
1539
desktop keyboard[CLS] the keyboard , which generally felt okay even for someone used to a desktop keyboard , now looks terrible . [SEP]
1540
display[CLS] the display is awesome . [SEP]
1541
warranty[CLS]

In [60]:
all_data[1]['text_raw']

'[CLS] i charge it at night and skip taking the cord with me because of the good battery life . [SEP]'

In [131]:
aspect_list=['cord', 'battery life']

In [132]:
aspect='battery life'

In [133]:
aspect_list

['cord', 'battery life']

In [134]:
aspect_list.remove(aspect)

In [135]:
aspect_list

['cord']

In [136]:
l = ['no surfing', 'flippers']

In [137]:
 l.remove('no surfing')

In [138]:
l

['flippers']

In [153]:

from data_utils import build_tokenizer, build_embedding_matrix, Tokenizer4Bert, ABSADataset
trainset = ABSADataset(opt.dataset_file['train'], tokenizer)

TypeError: 'int' object is not iterable

In [149]:
idx=0
while idx in range(len(all_data)):
    print(1)

1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


...

1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


KeyboardInterrupt: 

In [2]:
A = torch.Tensor([[[2, 3, 1], [1, 4, 0], [1, 0, 0]], [[2, 2, 0], [2, 0, 0], [3, 1, 4]]])
print(A.size())

B = torch.Tensor([[3, 2, 1], [2, 1, 3]]).long()
print(B.size())
B = B.view(2, 3, -1)
B = B - 1

C = torch.gather(A, 2, B)
print(C)

torch.Size([2, 3, 3])
torch.Size([2, 3])
tensor([[[1.],
         [4.],
         [1.]],

        [[2.],
         [2.],
         [4.]]])


In [3]:
A

tensor([[[2., 3., 1.],
         [1., 4., 0.],
         [1., 0., 0.]],

        [[2., 2., 0.],
         [2., 0., 0.],
         [3., 1., 4.]]])

In [4]:
A.shape

torch.Size([2, 3, 3])

In [7]:
B=A[:,bert_compete_cls_pos,:]

NameError: name 'bert_compete_cls_pos' is not defined

In [6]:
B

tensor([[[2., 3., 1.],
         [1., 4., 0.],
         [1., 0., 0.]],

        [[2., 2., 0.],
         [2., 0., 0.],
         [3., 1., 4.]]])

In [13]:
torch.gather(B, 1, index=torch.tensor([0,1,2]))

RuntimeError: invalid argument 4: Index tensor must have same dimensions as input tensor at /tmp/pip-req-build-4baxydiv/aten/src/TH/generic/THTensorEvenMoreMath.cpp:638

In [29]:
a = torch.Tensor([[1,2,3],
                  [4,5,6]])
index_1 = torch.LongTensor([[0,1],[2,0]])
# index_2 = torch.LongTensor([[0,1,1],[0,0,0]])
print(torch.gather(a, dim=1, index=index_1))
print(torch.gather(a, dim=0, index=index_2))


tensor([[1., 2.],
        [6., 4.]])
tensor([[1., 5., 6.],
        [1., 2., 3.]])


In [43]:
x = torch.randn(3,4,5)
print(x)
print(x.shape)
indices = torch.tensor([0,1,2])
cls_eb=x[range(len(x)),indices,:]
print(cls_eb)

tensor([[[ 1.0615e+00,  1.3872e+00,  5.1191e-01, -5.9119e-01, -1.4278e-01],
         [-2.4142e+00,  8.9777e-01,  1.0944e+00, -8.4538e-01, -1.7746e+00],
         [-2.4750e+00,  1.1911e-03,  1.3647e+00, -1.8695e+00, -1.3810e+00],
         [ 2.9760e-01,  3.9209e-01,  6.6058e-01, -1.0679e+00,  1.2657e+00]],

        [[ 2.9848e-01,  1.6469e+00, -3.3807e-01,  1.4091e-01, -1.1891e+00],
         [-7.6738e-01,  1.1700e+00,  5.1844e-01,  1.7250e+00, -8.6597e-01],
         [ 5.1901e-01,  9.3800e-01, -1.0659e+00, -1.4855e+00, -8.0697e-01],
         [-9.9978e-03, -8.8162e-01, -4.0575e-01, -1.3827e+00, -3.4041e-01]],

        [[ 1.8297e+00,  4.1491e-01, -1.6520e+00, -1.9126e-01,  1.3880e+00],
         [-7.0828e-01,  1.2704e+00,  2.0442e-01, -2.3010e+00,  8.3776e-01],
         [-4.4638e-01,  6.8099e-01, -7.4934e-01, -2.5877e+00,  4.2164e-01],
         [ 3.8602e-02, -1.9122e+00,  1.3171e-01,  1.2047e+00, -8.0233e-01]]])
torch.Size([3, 4, 5])
tensor([[ 1.0615,  1.3872,  0.5119, -0.5912, -0.1428],
     